# More reductions in memory

In this benchmark we will compare ironArray's performance with Zarr, HDF5, Numpy and TileDB. We will work with the data used in the [Reductions tutorial](../tutorials/05.Reductions.html) with the default chunk shapes for every library and compute the same reduction for every case with in memory operands.  It is important to stress that we are using defaults for every library, which are typically fine tuned for general performance; this is a pretty fair way to compare them without spending long time optimizing for every one.


Let's go:

In [1]:
%load_ext memprofiler

import numpy as np
import iarray as ia
import os
import zarr
import dask.array as da
import h5py
import hdf5plugin as h5plugin
from numcodecs import Blosc
import tiledb

In [2]:
!du -sh ../tutorials/precip-3m.iarr

672M	../tutorials/precip-3m.iarr


## Data

In [3]:
%%time

ia_precip = ia.load("../tutorials/precip-3m.iarr")
print(ia_precip.shape)
print("cratio: ", round(ia_precip.cratio, 2))
chunks = ia_precip.chunks
print(ia_precip.info)

(3, 720, 721, 1440)
cratio:  15.43
type   : IArray
shape  : (3, 720, 721, 1440)
chunks : (1, 128, 128, 256)
blocks : (1, 16, 32, 64)
cratio : 15.43

CPU times: user 21.7 ms, sys: 633 ms, total: 654 ms
Wall time: 973 ms


In [4]:
%%time
precip = ia_precip.data

CPU times: user 8.41 s, sys: 3.1 s, total: 11.5 s
Wall time: 7.34 s


In [5]:
precip_zarr = zarr.array(ia_precip.data)
print(precip_zarr.info)
precip_zdask = da.from_zarr(precip_zarr)

Type               : zarr.core.Array
Data type          : float32
Shape              : (3, 720, 721, 1440)
Chunk shape        : (1, 90, 91, 180)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : builtins.dict
No. bytes          : 8970393600 (8.4G)
No. bytes stored   : 1117920644 (1.0G)
Storage ratio      : 8.0
Chunks initialized : 1536/1536



In [6]:
# TileDB does not come with defaults for chunk shape (tiles), so using ironArray's one
shape = ia_precip.shape
adom = tiledb.Domain(
        tiledb.Dim(name="rows", domain=(0, shape[0] - 1), dtype=np.int32, tile=chunks[0]),
        tiledb.Dim(name="cols", domain=(0, shape[1] - 1), dtype=np.int32, tile=chunks[1]),
        tiledb.Dim(name="else", domain=(0, shape[2] - 1), dtype=np.int32, tile=chunks[2]),
        tiledb.Dim(name="else2", domain=(0, shape[3] - 1), dtype=np.int32, tile=chunks[3]),
    )

filters = tiledb.FilterList([tiledb.ByteShuffleFilter(), tiledb.LZ4Filter(5)])
aschema = tiledb.ArraySchema(
    domain=adom,  sparse=False, attrs=[tiledb.Attr(name="a", dtype=np.float32, filters=filters)]
)

# Create the (empty) array on disk.
tiledb_name = "mem://precip-3m-optimal.tiledb"
if not os.path.exists(tiledb_name):
    tiledb.DenseArray.create(tiledb_name, aschema)
    with tiledb.DenseArray(tiledb_name, mode="w") as A_opt:
        A_opt[:] = ia_precip.data

dask_tiledb = da.from_tiledb(tiledb_name, attribute='a')

## Std

### ironArray

In [7]:
%%mprof_run 1.iarray::std_memory
ia_reduc = ia.std(ia_precip, axis=(3, 0)).data

memprofiler: used -44.66 MiB RAM (peak of 3.18 MiB) in 9.6132 s, total RAM usage 1135.04 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [8]:
%%mprof_run 5.numpy::std_memory
np_reduc = np.std(precip, axis=(3, 0))

memprofiler: used -1087.46 MiB RAM (peak of 9469.61 MiB) in 73.8096 s, total RAM usage 47.66 MiB


In [9]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [10]:
%%mprof_run 2.zarr::std_memory
zdask_reduc = da.std(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used 1131.90 MiB RAM (peak of 8111.87 MiB) in 10.2785 s, total RAM usage 1285.21 MiB


In [11]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [12]:
h5_urlpath = "precip-3m.hdf5"

if not os.path.exists(h5_urlpath):
    with h5py.File(h5_urlpath, "w") as f:
        h5_precip = f.create_dataset("h5_precip", ia_precip.shape, dtype=ia_precip.dtype, **h5plugin.Blosc())
        ia_precip.copyto(h5_precip)


h5_file = h5py.File(h5_urlpath, "r", driver='core', backing_store=False)
precip_h5 = h5_file['h5_precip']


precip_h5dask = da.from_array(precip_h5)

h5_reduc_urlpath = "reduc.hdf5"
ia.remove_urlpath(h5_reduc_urlpath)

In [13]:
%%mprof_run 3.hdf5::std_memory

h5dask_reduc = da.std(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used -35.55 MiB RAM (peak of 5131.86 MiB) in 19.2979 s, total RAM usage 2341.29 MiB


In [14]:
del h5dask_reduc
del h5_reduc

### TileDB

In [15]:
%%mprof_run 4.tiledb::std_memory
res_dask_opt = da.std(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

memprofiler: used 70.59 MiB RAM (peak of 5153.83 MiB) in 23.0833 s, total RAM usage 2412.44 MiB


In [16]:
del res_dask_opt
tiledb.remove("mem://res_tiledb")

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [17]:
%mprof_plot .*::std

## max

### ironArray

In [18]:
%%mprof_run 1.iarray::max_memory
ia_reduc = ia.max(ia_precip, axis=(3, 0)).data

memprofiler: used 671.50 MiB RAM (peak of 672.38 MiB) in 2.7121 s, total RAM usage 3088.62 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [19]:
%%mprof_run 5.numpy::max_memory
np_reduc = np.max(precip, axis=(3, 0))

memprofiler: used 1117.65 MiB RAM (peak of 3406.83 MiB) in 21.7312 s, total RAM usage 4206.28 MiB


In [20]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [21]:
%%mprof_run 2.zarr::max_memory
zdask_reduc = da.max(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used -2892.87 MiB RAM (peak of 329.69 MiB) in 10.3195 s, total RAM usage 1379.07 MiB


In [22]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [23]:
%%mprof_run 3.hdf5::max_memory

h5dask_reduc = da.max(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used -815.12 MiB RAM (peak of 2827.29 MiB) in 26.7209 s, total RAM usage 572.17 MiB


In [24]:
del h5dask_reduc
del h5_reduc

### TileDB

In [25]:
%%mprof_run 4.tiledb::max_memory
res_dask_opt = da.max(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

memprofiler: used 132.36 MiB RAM (peak of 4439.76 MiB) in 18.5223 s, total RAM usage 793.84 MiB


In [26]:
del res_dask_opt
tiledb.remove("mem://res_tiledb")

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [27]:
%mprof_plot .*::max

## median

### ironArray

In [28]:
%%mprof_run 1.iarray::median_memory
ia_reduc = ia.median(ia_precip, axis=(3, 0)).data

memprofiler: used 782.36 MiB RAM (peak of 789.59 MiB) in 21.0580 s, total RAM usage 1665.11 MiB


### NumPy

Let's do the same computation with NumPy. First we will get the NumPy array from the ironArray one:

and now the actual reduction:

In [29]:
%%mprof_run 5.numpy::median_memory
np_reduc = np.median(precip, axis=(3, 0))

memprofiler: used -1623.96 MiB RAM (peak of 5556.00 MiB) in 73.8892 s, total RAM usage 41.20 MiB


In [30]:
np.testing.assert_allclose(ia_reduc, np_reduc, atol=1e-5, rtol=1e-5)
del np_reduc

### Zarr

In [31]:
%%mprof_run 2.zarr::median_memory
zdask_reduc = da.median(precip_zdask, axis=(3, 0))
zarr_reduc = zarr.create(shape=ia_reduc.shape, dtype=ia_reduc.dtype)
da.to_zarr(zdask_reduc, zarr_reduc)

memprofiler: used 1079.19 MiB RAM (peak of 8445.09 MiB) in 13.3489 s, total RAM usage 1227.56 MiB


In [32]:
np.testing.assert_almost_equal(zarr_reduc, ia_reduc)
del zdask_reduc
del zarr_reduc

### HDF5

In [33]:
%%mprof_run 3.hdf5::median_memory

h5dask_reduc = da.median(precip_h5dask, axis=(3, 0))

f = h5py.File(h5_reduc_urlpath, "w", driver='core', backing_store=False)
h5_reduc = f.create_dataset(name=h5_reduc_urlpath, shape=ia_reduc.shape, dtype=ia_reduc.dtype, **h5plugin.Blosc())
da.to_hdf5(h5_reduc_urlpath, '/x', h5dask_reduc)
f.close()

memprofiler: used -17.57 MiB RAM (peak of 5557.05 MiB) in 28.3179 s, total RAM usage 1217.98 MiB


In [34]:
del h5dask_reduc
del h5_reduc

### TileDB

In [35]:
%%mprof_run 4.tiledb::median_memory
res_dask_opt = da.median(dask_tiledb, axis=(3, 0))
res_dask_opt.to_tiledb("mem://res_tiledb")

memprofiler: used -683.53 MiB RAM (peak of 8308.06 MiB) in 25.6521 s, total RAM usage 593.16 MiB


In [36]:
del res_dask_opt
del dask_tiledb
tiledb.remove("mem://res_tiledb")

### Results

Finally, we will do a plot of the memory and time consumption with each different library.

In [37]:
%mprof_plot .*::median